In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

#### Reading the file and sorting based on timestamp

In [2]:
gaze_data = pd.read_csv('gaze_positions.csv')
gaze_data = gaze_data.sort_values(by=["gaze_timestamp"], 
                    ascending=[True])


#### Filtering out the calibration sequence

In [3]:
import copy
startTime = 0
endTime = 70



gaze_data['timestamp_sec'] = np.array(gaze_data['gaze_timestamp'] - gaze_data['gaze_timestamp'].iloc[0])
calibration_data = copy.deepcopy(gaze_data[np.logical_and(gaze_data['timestamp_sec'] >= startTime,gaze_data['timestamp_sec'] < endTime)])

#### Get 3 point coordinates
This is reusable function to get any 3point coordinates from the file

In [4]:
def get_3d_coordinates(row,coordinates_name):
    return [row['{}_x'.format(coordinates_name)],row['{}_y'.format(coordinates_name)],row['{}_z'.format(coordinates_name)]]

#### Get spherical coordinates
This is a reusable function to convert any cartesan coordinates to spherical coordinates

In [5]:
def get_spherical_coordinates(row,coordinates_name):
    coordinates = get_3d_coordinates(row,coordinates_name)
    az = np.rad2deg(np.arctan(np.divide(coordinates[0],coordinates[2])))
    el = np.rad2deg(np.arctan(np.divide(coordinates[1],coordinates[2])))
    return [az,el]

#### Get gaze point in world camera
This is done by converting the 3d gaze point from cartesan to spherical coordinates and then adding it as a new column in the csv file

In [6]:
azEl = calibration_data.apply(lambda arbitraryRowName: get_spherical_coordinates(arbitraryRowName,'gaze_point_3d'),axis=1)
calibration_data['gazeInWorldCam_az'],calibration_data['gazeInWorldCam_el'] = zip(*azEl)
list(calibration_data)

['gaze_timestamp',
 'world_index',
 'confidence',
 'norm_pos_x',
 'norm_pos_y',
 'base_data',
 'gaze_point_3d_x',
 'gaze_point_3d_y',
 'gaze_point_3d_z',
 'eye_center0_3d_x',
 'eye_center0_3d_y',
 'eye_center0_3d_z',
 'gaze_normal0_x',
 'gaze_normal0_y',
 'gaze_normal0_z',
 'eye_center1_3d_x',
 'eye_center1_3d_y',
 'eye_center1_3d_z',
 'gaze_normal1_x',
 'gaze_normal1_y',
 'gaze_normal1_z',
 'timestamp_sec',
 'gazeInWorldCam_az',
 'gazeInWorldCam_el']

#### Plotting Azimuth and elevation

### My Scatter Plot [This didn't work]

In [7]:

# fig = go.Figure([go.Scatter(x=plIndex, y=gaze_data['gazeInWorldCam_az'])])
# fig.show()
# fig = go.Figure([go.Scatter(x=plIndex, y=gaze_data['gazeInWorldCam_el'])])
# fig.show()

# traces = []
# az_plot = go.Scatter(x=calibration_data['timestamp_sec'], y=calibration_data['gazeInWorldCam_az'], marker_color = 'rgba(37, 99, 235, 0.8)', marker_size = 5, name = 'Azimuth')
# traces.append(az_plot)
# el_plot = go.Scatter(x=calibration_data['timestamp_sec'], y=calibration_data['gazeInWorldCam_el'], marker_color = 'rgba(44, 198, 237, 0.8)', marker_size = 5, name = 'Elevation')
# traces.append(el_plot)

# yLim=[-50,50]
# layout = dict(
#     dragmode= 'pan',
#     yaxis=dict(range=yLim, title='Degree'),
#     xaxis=dict(
#         rangeslider=dict(visible=True),title ='Time in sec'
#     )
# )


# fig = go.Figure(
#     data = traces,
#     layout = layout
# )
# fig.show()



In [8]:
# init_notebook_mode(connected=True)
from plotly.subplots import make_subplots


yLim=[-50,50]
width=800
height=600
inline=True

colors_idx = ['rgb(0,204,204)','rgb(128,128,128)','rgb(204,0,0)','rgb(102,0,204)']

traces = []

eih_el = go.Scattergl(
    x=calibration_data['timestamp_sec'],
    y=calibration_data['gazeInWorldCam_el'],
    name = 'gazeInWorldCam_el',
    marker_color = colors_idx[0],
    mode='markers',
    marker_size = 5,
    opacity = 0.8)

traces.append(eih_el)

eih_az = go.Scattergl(
    x=calibration_data['timestamp_sec'],
    y=calibration_data['gazeInWorldCam_az'],
    name = 'gazeInWorldCam_az',
    marker_color = colors_idx[1],
    mode='markers',
    marker_size = 5,
    opacity = 0.8)

traces.append(eih_az)

layout = dict(
    dragmode= 'pan',
    yaxis=dict(range=yLim, title='Degree'),
    xaxis=dict(
        rangeslider=dict(visible=True),title ='Time in sec'
    )
)


fig = go.Figure(data=traces, layout=layout)


iplot(fig)


In [9]:
# To get the timestamp for the calibration sequence and calculate
calibration_data['vidTimeStamp'] = np.array(calibration_data['gaze_timestamp'] - calibration_data['gaze_timestamp'].iloc[0])
calibration_data['change_in_time'] = calibration_data['vidTimeStamp'].diff()


calibration_data['angular_velocity_az'] = (calibration_data['gazeInWorldCam_az'].diff())
calibration_data['angular_velocity_el'] = (calibration_data['gazeInWorldCam_el'].diff())

calibration_data['angular_velocity'] = round((np.abs(np.sqrt(calibration_data['angular_velocity_az']**2  + calibration_data['angular_velocity_el']**2) / calibration_data['change_in_time'])),2)


angular_velocity_description = calibration_data['angular_velocity'].describe()
threshold = angular_velocity_description['75%']


In [10]:
vel = go.Scattergl(
    x=calibration_data['timestamp_sec'][0:16045],
    y=calibration_data['angular_velocity'][0:16045],
    name = 'velInWorldCam_az',
    marker_color = colors_idx[1],
    mode='lines+markers',
    marker_size = 5,
    opacity = 0.8)

# fig.append_trace(eih_el, row=1, col=1)
# fig.append_trace(eih_az, row=1, col=1)

vel_fig = dict(data=vel)

iplot(vel_fig)

#### Calculating using I-VT algorithm

In [11]:


def IVT_threshold(angular_velocity,threshold):
    idx=np.where(angular_velocity <= threshold)
    
    saccades = np.split(idx[0],np.array(np.where(np.diff(idx) > 1)[1]+1))
    sequence = []
    for s in saccades:
        if len(s) > 1:
            sequence.append((np.min(s), np.max(s)))
        else:
            sequence.append(s[0])
    return (sequence) 

saccade_group = (IVT_threshold(calibration_data['angular_velocity'],threshold))
print(len(saccade_group))

913


In [12]:
width=800
height=800
inline=True

from plotly.subplots import make_subplots
fig = make_subplots(rows=2, cols=1,shared_xaxes=True)

colors_idx = ['rgb(0,204,204)','rgb(128,128,128)','rgb(204,0,0)','rgb(102,0,204)']



eih_el = go.Scattergl(
    x=calibration_data['timestamp_sec'],
    y=calibration_data['gazeInWorldCam_el'],
    name = 'gazeInWorldCam_el',
    marker_color = colors_idx[0],
    mode='lines+markers',
    marker_size = 5,
    opacity = 0.8)

eih_az = go.Scattergl(
    x=calibration_data['timestamp_sec'],
    y=calibration_data['gazeInWorldCam_az'],
    name = 'gazeInWorldCam_az',
    marker_color = colors_idx[1],
    mode='lines+markers',
    marker_size = 5,
    opacity = 0.8)

vel = go.Scattergl(
    x=calibration_data['timestamp_sec'],
    y=calibration_data['angular_velocity'],
    name = 'velInWorldCam_az',
    marker_color = colors_idx[1],
    mode='lines+markers',
    marker_size = 5,
    opacity = 0.8)

fig.append_trace(eih_el, row=1, col=1)
fig.append_trace(eih_az, row=1, col=1)

# fig.append_trace(saccTraces, row=1, col=1)

fig.append_trace(vel, row=2, col=1)

fig.update_yaxes(range=[-50, 50], row=1, col=1)
fig.update_yaxes(range=[0, 200], row=2, col=1)


fig.update_yaxes(title = 'por (deg)',row=1,col=1)
fig.update_yaxes(title = 'vel (deg/s)',row=2,col=1)
fig.update_xaxes(title = 'time (s)',row=3,col=1)


layout = dict(
    dragmode= 'pan',
    title='Time Series with Rangeslider',
    width=width,
    height=height,
    yaxis=dict(range=yLim, title='angular position (degrees)'),
)



fig.update_layout(legend_orientation="h", 
             xaxis2_rangeslider_visible=True, xaxis2_rangeslider_thickness=0.1,
                  xaxis2_rangeslider_range=[0,70],
                 )

iplot(fig)

#### Plotting the saccade point

In [13]:

def drawPatch(startTime,stopTime, y0, y1):

    patchTrace = go.Scattergl(x=[startTime,stopTime,stopTime,startTime],
                              y=[y0,y0,y1, y1],
                              mode='lines',
                              line = dict(
                                  color='rgba(20, 0, 145,0.6)',
                                  width = 1),
                              fill="toself",
                              showlegend=False,
    )
    
    return patchTrace

In [14]:


min_idx = []
max_idx = []

for z in saccade_group:
    min_idx.append(np.min(z))
    max_idx.append(np.max(z))

startTime = np.array(calibration_data['timestamp_sec'].iloc[min_idx])
endTime = np.array(calibration_data['timestamp_sec'].iloc[max_idx])

for secsStart, secsStop in zip(startTime, endTime):
    fig.append_trace(drawPatch(secsStart,secsStop,-50, 50),row=1, col=1)
    fig.append_trace(drawPatch(secsStart,secsStop,0, 200),row=2, col=1)

iplot(fig)
    

# # Iterate through each start/stop pair and plot!  
# # Note that the third and fourth arguments are the ymin/max of my axes. 
# for secsStart, secsStop in zip(saccadeStartTimeSecs, saccadeEndTimeSecs):
#     fig.append_trace(drawPatch(secsStart,secsStop,-50, 50),row=1, col=1)
#     fig.append_trace(drawPatch(secsStart,secsStop,0, 200),row=2, col=1)
    

# # Plot it!
# iplot(fig)

In [15]:
# def drawPatch(startTime,stopTime):

#     patchTrace = go.Scattergl(x=[startTime,stopTime], y=[-100,100,-100,100],
#                               mode='lines',
#                               line = dict(
#                                   color='rgba(0,0,0,0.2)',
#                                   width = 2),
#                               fill="toself",
#                               showlegend=False,
#     )
#     return patchTrace

# fig = go.Figure(
#     data = traces,
#     layout = layout
# )

# for z in ((saccade_group)):
#     min_idx = np.min(z)
#     max_idx = np.max(z)
#     # print(calibration_data['timestamp_sec'].iloc[min_idx],calibration_data['timestamp_sec'].iloc[max_idx])
#     # drawPatch(calibration_data['timestamp_sec'].iloc[min_idx],calibration_data['timestamp_sec'].iloc[max_idx], -1000,1000)
#     fig.add_vrect(
#         x0 = calibration_data['timestamp_sec'].iloc[min_idx],
#         x1 = calibration_data['timestamp_sec'].iloc[max_idx],
#         opacity = 0.2,
#         line_width=0
#         )


# fig.show()

